In [1]:
import pandas as pd
import geopandas as gpd
import shapely
from shapely.geometry import Polygon, Point, MultiPoint
import math
import matplotlib.pyplot as plt
import numpy as np
from numpy import exp
from numpy.random import rand, seed
import folium
import random 
import osmnx as ox
import networkx as nx
pd.options.mode.chained_assignment = None  # default='warn'

In [2]:
# a10 boundary
a10 = gpd.read_file('data/A10.shp')
a10 = a10.to_crs('EPSG:28992')
a10 = a10.to_crs('EPSG:4326')

# factory distances
# to add data from route planner: 
# https://www.routescanner.com/app/voyages-search
timberFactory_coords = [50.91608687148152, 5.837795943482761]
concreteFactor_coords = [51.472216701413025, 5.737978710264017]
moduleFactory_coords = [51.218521, 9.637029]
data = {
    'material': ['timber', 'concrete', 'modules'], 
    'distFromAms_km': [500, 250, 350], # dummy number 
    'x': [timberFactory_coords[1], concreteFactor_coords[1], moduleFactory_coords[1]],
    'y': [timberFactory_coords[0], concreteFactor_coords[0], moduleFactory_coords[0]]
}
suppliers = pd.DataFrame(data)
suppliers = gpd.GeoDataFrame(suppliers, crs='EPSG:4326',
                             geometry=gpd.points_from_xy(suppliers.x, suppliers.y))
suppliers = suppliers.to_crs('EPSG:28992')
suppliers = suppliers.drop(columns=['x', 'y'])
suppliers = suppliers.to_crs('EPSG:4326')

# construction project locations and materials 
conSites_df = pd.read_csv('data/constructionSites.csv')
conSites_df = conSites_df.dropna(how='all').dropna(axis=1)
conSites_df.rename(columns={
    'Project name': 'name', 
    'Latitude': 'lat', 
    'Longitude': 'lon', 
    'Developer': 'developer', 
    'Status': 'status', 
    'Type': 'material'
}, inplace=True)

conSites_gdf = gpd.GeoDataFrame(
    conSites_df, 
    geometry=gpd.points_from_xy(conSites_df.lon, conSites_df.lat), 
    crs='EPSG:4326')
conSites_gdf = conSites_gdf.to_crs('EPSG:28992')
conSites_gdf = conSites_gdf[['name', 'geometry']]
conSites = conSites_gdf.copy() #.sample(20)

buildingType_list = ['A', 'B', 'C', 'D', 'E']
conSites['buildingType'] = np.random.choice(buildingType_list, size=len(conSites))
conSites['inA10'] = conSites.geometry.within(a10.geometry[0])
conSites = conSites.to_crs('EPSG:4326')

# hub locations for three scenarios: none, centralized, decentralized
minx, miny, maxx, maxy = conSites_gdf.total_bounds
candiHubs = gpd.read_file('data/candiHubs_ams.shp')
candiHubs = candiHubs.cx[minx:maxx, miny:maxy]
microHubs = candiHubs.sample(10)
microHubs['hub_type'] = 'micro'
macroHubs = pd.read_csv('data/data_construction_hubs.csv')
macroHubs = gpd.GeoDataFrame(
    macroHubs, 
    geometry=gpd.points_from_xy(macroHubs.Longitude, macroHubs.Latitude),
    crs='EPSG:4326'
)
macroHubs.rename(columns={'Name': 'name', 'Type': 'hub_type'}, inplace=True)
macroHubs = macroHubs[['name', 'hub_type', 'geometry']]
macroHubs = macroHubs.to_crs('EPSG:28992')
hubs = pd.concat([macroHubs, microHubs]).reset_index(drop=True)
hubs = hubs.reset_index(names='hub_id')
hubs = hubs[['hub_id', 'hub_type', 'geometry']]
macro = hubs[hubs.hub_type == 'macro']
hubs['nearestMacroHub'] = macro.geometry.sindex.nearest(list(hubs.geometry))[1]
hubs['inA10'] = hubs.geometry.within(a10.geometry[0])
hubs = hubs.to_crs('EPSG:4326')

# make dummy data for material required per building type 
data_structural = {
    'buildingType': ['A', 'A', 'A', 'B', 'B', 'B', 'C', 'C', 'C', 'D', 'D', 'D', 'E', 'E', 'E'],
    'biobased': ['none', 'semi', 'full', 'none', 'semi', 'full', 'none', 'semi', 'full', 'none', 'semi', 'full', 'none', 'semi', 'full'],
    'concrete': [5000, 3000, 1000, 5000, 3000, 1000, 5000, 3000, 1000, 5000, 3000, 1000, 5000, 3000, 1000],
    'timber': [0, 2000, 4000, 0, 2000, 4000, 0, 2000, 4000, 0, 2000, 4000, 0, 2000, 4000],
}

data_nonStructural = {
    'buildingType': ['A', 'A', 'A', 'B', 'B', 'B', 'C', 'C', 'C', 'D', 'D', 'D', 'E', 'E', 'E'],
    'biobased': ['none', 'semi', 'full', 'none', 'semi', 'full', 'none', 'semi', 'full', 'none', 'semi', 'full', 'none', 'semi', 'full'],
    'concrete': [50, 50, 50, 50, 50, 50, 50, 50, 50, 50, 50, 50, 50, 50, 50],
    'timber': [50, 400, 600, 50, 400, 600, 50, 400, 600, 50, 400, 600, 50, 400, 600],
}
data_nUnits = {
    'buildingType': ['A', 'B', 'C', 'D', 'E'],
    'modules': [47, 46, 54, 52, 52]
}
nUnits = pd.DataFrame(data_nUnits)
materialPerBiobasedType_structural = pd.DataFrame(data_structural)
materialPerBiobasedType_structural['strucType'] = 'structural'
materialPerBiobasedType_nonstructural = pd.DataFrame(data_nonStructural)
materialPerBiobasedType_nonstructural['strucType'] = 'nonstructural'
material_perBiobasedType = pd.concat([materialPerBiobasedType_structural, materialPerBiobasedType_nonstructural])
for mat in ['concrete', 'timber']: 
    material_perBiobasedType[mat] = material_perBiobasedType[mat].map(lambda x: x+random.randint(50,500))
material_perBiobasedType = pd.merge(material_perBiobasedType, nUnits)
    
# vehicle capacities
data = {
    'transType': ['road', 'road', 'roadWater', 'rail'],
    'vehicleType': ['diesel', 'electric', 'roadWater', 'rail'],
    'capacity_timber': [20, 20, 50, 45],
    'capacity_concrete': [25, 25, 60, 70],
    'capacity_modules': [2, 2, 3, 5],
    'emissions_perKm': [0.0009, 0, 0.0007, 0.0006]
}
vehicleCapacity_df = pd.DataFrame(data)

# to add: demolition site locations 
# to add: street network

In [3]:
suppliers.rename(columns={'distFromAms_km': 'distAms'}, inplace=True)
conSites.rename(columns={'buildingType': 'buildType'}, inplace=True)
hubs.rename(columns={'nearestMacroHub': 'nearMacro'}, inplace=True)
suppliers_csv = suppliers[['material', 'distAms']]

In [149]:
# gdf of supply of secondary resources 
supplyFile = gpd.read_file('../_bigData/pblUrbanMiningModels/shpsCleaned/supply_NL.shp')
supplyFile = supplyFile.reset_index(drop=True)

sites = conSites.copy()
xmin, ymin, xmax, ymax = sites.to_crs('EPSG:28992').total_bounds
buffer = 15000
xmin, ymin = xmin-buffer, ymin-buffer
xmax, ymax = xmax+buffer, ymax+buffer

supply = supplyFile.copy()
supply = supply.cx[xmin:xmax, ymin:ymax]

supply = supply[(supply.buildYear > 1920) & (supply.buildYear < 1980)]
supply = supply.sort_values('buildYear')
nRows = int(len(supply) / 1) # oldest 1/6 of cells  
supply = supply.head(nRows)
supply.buildYear = supply.buildYear.map(lambda x: int(math.floor(x)))
supply = supply[['buildYear', 'class', 
                 'steel', 'copper', 'aluminium', 'wood', 
                 'concrete', 'brick', 'glass','ceramic', 
                 'plastic', 'insulat', 'geometry']]
for mat in ['steel', 'copper', 'aluminium', 'wood', 'concrete', 
            'brick', 'glass','ceramic', 'plastic', 'insulat']: 
    supply[mat] = supply[mat].map(lambda x: x/1000)
supply.rename(columns={'wood': 'timber', 'insulat': 'insulation'}, inplace=True)
demSites = supply.copy()
demSites = demSites.reset_index(drop=True).reset_index(names='id')
demSites = demSites.to_crs('EPSG:4326')
demSites_hires = demSites.copy()

# simplify demSites to grid of 1km by 1km rather than 100m by 100m 
def compute_grid_cell(point, size=1000):
    x, y = point.x, point.y
    x_min, x_max = x - (x % size), x - (x % size) + size
    y_min, y_max = y - (y % size), y - (y % size) + size
    return Polygon([(x_min, y_min), (x_min, y_max), (x_max, y_max), (x_max, y_min)])
demSites = demSites.to_crs('EPSG:28992')
demSites['grid_cell'] = demSites.geometry.apply(compute_grid_cell)
demSites = demSites.groupby('grid_cell', sort=False).sum(numeric_only=True).reset_index()
demSites = gpd.GeoDataFrame(demSites, geometry=demSites.grid_cell, crs='EPSG:28992')
demSites.geometry = demSites.geometry.centroid
demSites = demSites.to_crs('EPSG:4326')
demSites.drop(columns=['grid_cell', 'id', 'buildYear'], inplace=True)

In [106]:
a10.to_file('data/data_cleaned/a10.shp')
suppliers.to_file('data/data_cleaned/suppliers.shp')
conSites.to_file('data/data_cleaned/construction_sites.shp')
demSites.to_file('data/data_cleaned/demolition_sites.shp')
hubs.to_file('data/data_cleaned/hubs.shp')
material_perBiobasedType.to_csv('data/data_cleaned/buildingType_info.csv')
vehicleCapacity_df.to_csv('data/data_cleaned/vehicles_info.csv')
suppliers_csv.to_csv('data/data_cleaned/suppliers.csv')

# street network

In [302]:
%%time

# make bounding box for MRA 
xmin, ymin, xmax, ymax = demSites.to_crs('EPSG:28992').total_bounds
bbox = Polygon([(xmin, ymin), (xmin, ymax), (xmax, ymax), (xmax, ymin)]).buffer(1000)
gdf = gpd.GeoDataFrame({'geometry': [bbox]}, crs="EPSG:28992")
xmin, ymin, xmax, ymax = gdf.to_crs('EPSG:4326').total_bounds

# fetch osmnx graph road network for MRA
custom_filter = '["highway"~"motorway|trunk|primary|secondary|tertiary"]'
G = ox.graph_from_bbox(ymax, ymin, xmax, xmin, network_type='drive', 
                          custom_filter=custom_filter) 
G = ox.utils_graph.get_largest_component(G, strongly=False)
G = G.to_undirected()

# fix speed limits 
default_speed = 50
for u, v, key, data in G.edges(keys=True, data=True):
    if 'maxspeed' not in data:
        data['maxspeed'] = default_speed
    elif isinstance(data['maxspeed'], list):
        data['maxspeed'] = [int(s) for s in data['maxspeed']]
        data['maxspeed'] = int(sum(data['maxspeed']) / len(data['maxspeed']))
    else: 
        data['maxspeed'] = int(data['maxspeed'])
        
# Add travel time (in minutes) for all edges
for u, v, key, data in G.edges(keys=True, data=True):
    data['time'] = data['length'] / (data['maxspeed'] * 1000) * 60

CPU times: total: 25.8 s
Wall time: 26.4 s


In [304]:
%%time 
# make unique_ids for gdfs of sites, suppliers, and hubs
# read files exactly the same way as model
sites = gpd.read_file('data/data_cleaned/construction_sites.shp')
suppliers = gpd.read_file('data/data_cleaned/suppliers.shp')
hubs = gpd.read_file('data/data_cleaned/hubs.shp')
demSites = gpd.read_file('data/data_cleaned/demolition_sites.shp')

# add ids exactly like the model 
sites['unique_id'] = pd.Series(range(len(sites)))
suppliers['unique_id'] = pd.Series(range(len(sites), 
                                         len(sites)+len(suppliers)))
hubs['unique_id'] = pd.Series(range(len(sites)+len(suppliers), 
                                    len(sites)+len(suppliers)+len(hubs)))
demSites['unique_id'] = pd.Series(range(len(sites)+len(suppliers)+len(hubs), 
                                        len(sites)+len(suppliers)+len(hubs)+len(demSites)))

def make_od_matrix(G, gdf_ori, gdf_dest): 
    od_matrix = []
    for _, ori_row in gdf_ori.iterrows():
        ori_point = ori_row.geometry
        ori_node = ox.distance.nearest_nodes(G, ori_point.x, ori_point.y)
        for _, dest_row in gdf_dest.iterrows():
            dest_point = dest_row.geometry
            dest_node = ox.distance.nearest_nodes(G, dest_point.x, dest_point.y)
            distance = nx.shortest_path_length(G, source=ori_node, target=dest_node, weight='time', method='dijkstra')
            od_matrix.append([ori_row.unique_id, dest_row.unique_id, round(distance/1000, 3)])
    return np.array(od_matrix)

def make_edgeIds_matrix(G, gdf_ori, gdf_dest): 
    edgeIds_matrix = []
    for _, ori_row in gdf_ori.iterrows():
        ori_point = ori_row.geometry
        ori_node = ox.distance.nearest_nodes(G, ori_point.x, ori_point.y)
        for _, dest_row in gdf_dest.iterrows():
            dest_point = dest_row.geometry
            dest_node = ox.distance.nearest_nodes(G, dest_point.x, dest_point.y)
            shortest_path = nx.shortest_path(G, ori_node, dest_node, weight='time', method='dijkstra')
            road_segments = [(shortest_path[i], shortest_path[i+1]) for i in range(len(shortest_path)-1)]
            edge_ids = [G[u][v][0]['osmid'] for u, v in road_segments]
            edge_ids = [','.join(map(str, e)) if isinstance(e, list) else str(e) for e in edge_ids]
            edgeIds_matrix.append([ori_row.unique_id, dest_row.unique_id, edge_ids])
    return np.array(edgeIds_matrix, dtype=object)

macroHubs = hubs[hubs.hub_type == 'macro']

od_matrix_h2c = make_od_matrix(G, hubs, sites)
od_matrix_h2h = make_od_matrix(G, macroHubs, hubs)
od_matrix_h2hc = np.vstack((od_matrix_h2c, od_matrix_h2h))
od_matrix_d2h = make_od_matrix(G, demSites, macroHubs)
od_matrix_s2h = make_od_matrix(G, suppliers, macroHubs)

edgeIds_matrix_h2c = make_edgeIds_matrix(G, hubs, sites)
edgeIds_matrix_h2h = make_edgeIds_matrix(G, macroHubs, hubs)
edgeIds_matrix_h2hc = np.vstack((edgeIds_matrix_h2c, edgeIds_matrix_h2h))
edgeIds_matrix_d2h = make_edgeIds_matrix(G, demSites, macroHubs)
edgeIds_matrix_s2h = make_edgeIds_matrix(G, suppliers, macroHubs)

CPU times: total: 3min 57s
Wall time: 4min 5s


In [305]:
# make nodes, edges gdf from graph G
nodes, edges = ox.graph_to_gdfs(G)

# select edges within edgeIds_matrix_all 
edges.osmid = edges.osmid.map(lambda x: ','.join(map(str,x)) if isinstance(x, list) else str(x))
edges = edges[['osmid', 'geometry']]
edges = edges.reset_index(drop=True)
edges['nTrips'] = 0
edgeIds_matrix_all = np.vstack((edgeIds_matrix_s2h, edgeIds_matrix_d2h, edgeIds_matrix_h2hc))
osmidList = [item for sublist in edgeIds_matrix_all[:, 2] for item in sublist]
osmidList = [','.join(map(str, item)) if isinstance(item, list) else str(item) for item in osmidList]
edges = edges[edges['osmid'].isin(osmidList)]

In [309]:
supplier_id = 30
od = od_matrix_s2h
od_s = od[od[:, 0] == supplier_id]
nearestHub_id = 32 # int(od_s[np.argmin(od_s[:, 2]), 1])

roadMatrix = edgeIds_matrix_s2h
roadIds = roadMatrix[(roadMatrix[:, 0] == supplier_id) & (roadMatrix[:, 1] == nearestHub_id)][0][2]

path = edges[edges.osmid.isin(roadIds)]
supplier = suppliers[suppliers.unique_id == supplier_id]
hub = hubs[hubs.unique_id == nearestHub_id]

m = folium.Map([52.377231, 4.899288], zoom_start=11, tiles='cartodbdark_matter')
for _, row in hub.iterrows(): 
    folium.CircleMarker([row.geometry.y, row.geometry.x], 
                        color='white', radius=3).add_to(m)
for _, row in supplier.iterrows(): 
    folium.CircleMarker([row.geometry.y, row.geometry.x], 
                        color='lightblue', radius=0.5).add_to(m)
for _, row in path.iterrows():
    folium.PolyLine([(lat, lon) for lat, lon in zip(row.geometry.xy[1], row.geometry.xy[0])],
                           color='red', weight=1.5).add_to(m)

m

In [307]:
%%time
# save gdfs to disk
ox.io.save_graphml(G, filepath="data/data_cleaned/ams_roads.graphml")
nodes.to_file('data/data_cleaned/ams_roads_nodes.shp')
edges.to_file('data/data_cleaned/ams_roads_edges.shp')

# save od matrices to disk 
np.save('data/data_cleaned/od_matrix_h2c.npy', od_matrix_h2c)
np.save('data/data_cleaned/od_matrix_h2h.npy', od_matrix_h2h)
np.save('data/data_cleaned/od_matrix_h2hc.npy', od_matrix_h2hc)
np.save('data/data_cleaned/od_matrix_d2h.npy', od_matrix_d2h)
np.save('data/data_cleaned/od_matrix_s2h.npy', od_matrix_s2h)

# save od matrices to disk 
np.save('data/data_cleaned/roadOsmIds_matrix_h2c.npy', edgeIds_matrix_h2c)
np.save('data/data_cleaned/roadOsmIds_matrix_h2h.npy', edgeIds_matrix_h2h)
np.save('data/data_cleaned/roadOsmIds_matrix_h2hc.npy', edgeIds_matrix_h2hc)
np.save('data/data_cleaned/roadOsmIds_matrix_d2h.npy', edgeIds_matrix_d2h)
np.save('data/data_cleaned/roadOsmIds_matrix_s2h.npy', edgeIds_matrix_s2h)

# save all shpfiles
suppliers.to_file('data/data_cleaned/suppliers.shp')
sites.to_file('data/data_cleaned/construction_sites.shp')
demSites.to_file('data/data_cleaned/demolition_sites.shp')
hubs.to_file('data/data_cleaned/hubs.shp')

<timed exec>:3: UserWarning: Column names longer than 10 characters will be truncated when saved to ESRI Shapefile.


CPU times: total: 5.75 s
Wall time: 6.16 s


In [308]:
%%time 
# read data 
edges = gpd.read_file('data/data_cleaned/ams_roads_edges.shp')
demSites = gpd.read_file('data/data_cleaned/demolition_sites.shp')
hubs = gpd.read_file('data/data_cleaned/hubs.shp')
conSites = gpd.read_file('data/data_cleaned/construction_sites.shp')

# visualize data 
m = folium.Map([52.377231, 4.899288], zoom_start=11, tiles='cartodbdark_matter')
for _, row in edges.iterrows():
    folium.PolyLine([(lat, lon) for lat, lon in zip(row.geometry.xy[1], row.geometry.xy[0])],
                           color='grey', weight=1.5).add_to(m)
for _, row in demSites.iterrows(): 
    folium.CircleMarker([row.geometry.y, row.geometry.x], 
                        color='lightblue', radius=0.5).add_to(m)
for _, row in hubs.iterrows(): 
    folium.CircleMarker([row.geometry.y, row.geometry.x], 
                        color='red', radius=3).add_to(m)
for _, row in conSites.iterrows(): 
    folium.CircleMarker([row.geometry.y, row.geometry.x], 
                        color='green', radius=3).add_to(m)
for _, row in suppliers.iterrows(): 
    folium.CircleMarker([row.geometry.y, row.geometry.x], 
                        color='lightblue', radius=0.5).add_to(m)

m

CPU times: total: 1.83 s
Wall time: 1.89 s
